In [ ]:
import gradio as gr
import numpy as np
from os import environ
from PIL import Image as PImage
from torchvision import transforms as T
from transformers import MaskFormerForInstanceSegmentation, MaskFormerImageProcessor

In [ ]:
ade_mean=[0.485, 0.456, 0.406]
ade_std=[0.229, 0.224, 0.225]

model_id = f"thiagohersan/maskformer-satellite-trees"

In [ ]:
# preprocessor = MaskFormerImageProcessor.from_pretrained(model_id)
preprocessor = MaskFormerImageProcessor(
    do_resize=False,
    do_normalize=False,
    do_rescale=False,
    ignore_index=255,
    reduce_labels=False
)

hf_token = environ.get('HFTOKEN') or True
model = MaskFormerForInstanceSegmentation.from_pretrained(model_id, use_auth_token=hf_token)

test_transform = T.Compose([
    T.ToTensor(),
    T.Normalize(mean=ade_mean, std=ade_std)
])

with PImage.open("../color-filter-calculator/assets/Artshack_screen.jpg") as img:
    img_size = (img.height, img.width)
    norm_image = test_transform(np.array(img))
    inputs = preprocessor(images=norm_image, return_tensors="pt")
    

In [ ]:
outputs = model(**inputs)

In [ ]:
results = preprocessor.post_process_semantic_segmentation(outputs=outputs, target_sizes=[img_size])[0]
results = results.numpy()

labels = np.unique(results)

In [ ]:
for label_id in labels:
    print(model.config.id2label[label_id])